#### Timeframes

- Longo Prazo: x >= 12 meses
- Medio Prazo: 3 <= x < 12 
- Curto Prazo: 1 <= x < 3
- Curtissimo Prazo: x < 1 mes


### 1. Atributo: Descentralizacao dos Mineradores

##### 1.1. Herfindahl-Hirschman Index (Longo Prazo)

$$HHI = \sum_{i=1}^{n} S_i^2$$

 - HHI >= 2500: high concentratation
 - 1500 <= HHI < 2500: moderate concentratation
 - HHI < 1500: low concentratation

*Data Source:* https://www.blockchain.com/pt/pools


In [1]:
import time
import pandas as pd
import seaborn as sns
from selenium import webdriver
import time

today = time.strftime("%Y-%m-%d")

url = 'https://www.blockchain.com/pt/pools'

# https://sites.google.com/a/chromium.org/chromedriver/getting-started
browser = webdriver.Chrome()
browser.get(url)

time.sleep(3)

html = browser.page_source

data = pd.read_html(html, attrs={'id': 'known_pools'}, header=0, flavor='bs4')[0]

browser.quit()

# Equation

hhi = ((data['contagem'] / data['contagem'].sum() * 100) **2).sum()

# to create .csv
# data = pd.DataFrame({'day':[today], 'hhi':[hhi]}).set_index('day')
# data.to_csv("./hhi.csv")

df = pd.read_csv("./hhi.csv", index_col='day', parse_dates=[0])

df.loc[today] = hhi

# save
df.to_csv("./hhi.csv")

df = df.reset_index()

# plot
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

trace1 = go.Scatter(x=df['day'], y=df['hhi'], name='HHI')

data = [trace1]

layout = go.Layout(
    title='HHI',
    yaxis=dict(
        title='HHI'
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

### 2. Atributo: Valoracao

##### 2.1. MVRV Ratio - Market Value to Realized Value (Longo Prazo)

$$MVRV Ratio = \frac{Valor de Mercado} {Valor Realizado}$$

- Euforia = Valor de mercado acima do valor realizado
- Medo Excessivo = Valor de mercado abaixo do valor realizado
- Indicador de Distorcoes na Valoracao

*Data Source:* https://coinmetrics.io/charts/#assets=btc_left=mvrv

In [2]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
init_notebook_mode(connected=True)

url = 'https://coinmetrics.io/data/btc.csv'

s=requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['MVRV'] = df['marketcap(USD)'] / df['realizedCap(USD)']

df['MVRV^-1'] = df['realizedCap(USD)'] / df['marketcap(USD)']

df = df[df['price(USD)'].notnull()]

trace1 = go.Scatter(x=df['date'], y=df['MVRV'], name='MVRV')

trace2 = go.Scatter(x=df['date'], y=df['MVRV^-1'], name='MVRV^-1')

trace3 = go.Scatter(x=df['date'], y=df['price(USD)'], name='Price', yaxis='y2')

data = [trace1, trace2, trace3]

layout = go.Layout(
    title='MVRV',
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 2.2. NVT Ratio - Network Value to Transactions ratio (Longo Prazo)

$$NVT Ratio = \frac{Network Value} {Volume}$$

$$NVT Signal = \frac{Network Value} {90 MA Volume}$$

- Alto = Preco Caro
- Baixo = Preco Barato 
- Indicador de Distorcoes no Preço/Valoração
- Liquid, Bitcoin`s first sidechain, went live 10 Oct 2018, taking volume off the main chain. NVTS will need recalibration.

*Data Sources:* 
- https://coinmetrics.io/nvt/#assets=btc_log=false_roll=1_left=NVT.kalichkin.adjusted
- http://charts.woobull.com/bitcoin-nvt-signal/
- https://medium.com/cryptolab/https-medium-com-kalichkin-rethinking-nvt-ratio-2cf810df0ab0


In [3]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
init_notebook_mode(connected=True)

url = 'https://coinmetrics.io/data/btc.csv'
days = 90

s=requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['NVTSAd'] = df['marketcap(USD)'] / (df['adjustedTxVolume(USD)'].rolling(window=days).mean())

df = df[df['NVTSAd'].notnull()]

trace1 = go.Scatter(x=df['date'], y=df['NVTSAd'], name='NVTSAdj')

trace2 = go.Scatter(x=df['date'], y=df['price(USD)'], name='Price', yaxis='y2')

trace3 = dict(x=df['date'], y=len(df) * [45], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#2ae40e'), stackgroup='one')

trace4 = dict( x=df['date'], y=len(df) * [10], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#FFFF00'), stackgroup='one')

trace5 = dict( x=df['date'], y=len(df) * [70], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#FF6347'), stackgroup='one')

data = [trace1, trace2, trace3, trace4, trace5]

layout = go.Layout(
    title='NVTS Adjusted',
    yaxis=dict(
        title='NVTSAdj'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

In [4]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

url = 'https://coinmetrics.io/data/btc.csv'
days = 90

s=requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['NVTS'] = df['marketcap(USD)'] / (df['txVolume(USD)'].rolling(window=days).mean())

df = df[df['NVTS'].notnull()]

trace1 = go.Scatter(x=df['date'], y=df['NVTS'], name='NVTS')

trace2 = go.Scatter(x=df['date'], y=df['price(USD)'], name='Price', yaxis='y2')

trace3 = dict(x=df['date'], y=len(df) * [20], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#2ae40e'), stackgroup='one')

trace4 = dict( x=df['date'], y=len(df) * [8], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#FFFF00'), stackgroup='one')

trace5 = dict( x=df['date'], y=len(df) * [70], mode='lines', hoverinfo='skip', showlegend=False, line=dict(width=0.5, color='#FF6347'), stackgroup='one')

data = [trace1, trace2, trace3, trace4, trace5]

layout = go.Layout(
    title='NVTS',
    yaxis=dict(
        title='NVTS'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

In [5]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://api.blockchain.info/charts/{i}?timespan=all&format=csv"

volume = pd.read_csv(io.StringIO(requests.get(url.format(i='estimated-transaction-volume-usd')).content.decode('utf-8')), parse_dates=[0], names=["date", "volume"])

market_cap = pd.read_csv(io.StringIO(requests.get(url.format(i='market-cap')).content.decode('utf-8')), parse_dates=[0], names=["date", "market_cap"])

price = pd.read_csv(io.StringIO(requests.get(url.format(i='market-price')).content.decode('utf-8')), parse_dates=[0], names=["date", "price"])

df = pd.merge(volume, market_cap, on='date').merge(price, on='date')

days = 90

df['NVTS'] = df['market_cap'] / (df['volume'].rolling(window=days).mean())

df = df[df['date'] > '2011-01-01']

trace1 = go.Scatter(x=df['date'], y=df['NVTS'], name='NVTS')

trace2 = go.Scatter(x=df['date'], y=df['price'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title="NVTS (Blockchain.info Data)",
    yaxis=dict(
        title='NVTS'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    ),
    shapes= [
        # Line Horizontal
        {
            'type': 'line',
            'x0': df.iloc[1].date,
            'y0': 100,
            'x1': df.iloc[-1].date,
            'y1': 100,
            'line': {
                'dash': 'dashdot',
            },
        },
        {
            'type': 'line',
            'x0': df.iloc[1].date,
            'y0': 40,
            'x1': df.iloc[-1].date,
            'y1': 40,
            'line': {
                'dash': 'dashdot',
            },
        }
    ]
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

### 3. Ciclo de Negocios do Bitcoin

##### 3.1. MPE Rate - Miner Profit Expansion Rate (Longo Prazo)

$$MPE Ratio_i = \sqrt[n]{\prod_{j=365}^{n}(\frac{Recompensa Por Bloco_i} {Recompensa Por Bloco_{i-1}})_j}$$

- Proxy de um indicador antecedente de longo prazo
- Taxa de crescimento de lucros dos mineradores tem uma tendencia anti persistente, retorno a media confirmado pelo Coeficiente de Hurst (E.g. Comodities, Taxa de crescimento de lucros de empresas)
- Regioes extremas sinalizam formações de grandes topos e fundos de mercado

*Data Source:* https://bitcoinvisuals.com/chain-block-reward

In [6]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

days = 365

s = requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['blockreward'] = df['blockreward_median'] * df['price_btc']

df = df[df['blockreward'].notnull()]

df['blockrewardshift'] = df['blockreward'].shift(1)

df['blockrewardrate'] = ((df['blockreward'] / df['blockrewardshift']) * 100)

df['blockrewardrategmean'] = (df['blockrewardrate']).rolling(window=days).apply(stats.gmean, raw=True) - 100

trace1 = go.Scatter(x=df['day'], y=df['blockrewardrategmean'], name='MPE Rate')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='MPE Rate',
    yaxis=dict(
        title='MPE'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 3.2. TFE Rate - Transaction Fee Expansion Rate (Longo Prazo)

$$TFE Ratio_i = \sqrt[n]{\prod_{j=365}^{n}(\frac{Taxa de Transacao_i} {Taxa de Transacao_{i-1}})_j}$$

- Baseada no MPE Rate
- Proxy de um indicador antecedente de longo prazo
- Regioes extremas sinalizam formações de grandes topos e fundos de mercado

*Data Source:* https://bitcoinvisuals.com/

In [7]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

days = 365

s = requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['tx_fee'] = df['tx_fee_mean_median'] * df['price_btc']

df = df[df['price_btc'].notnull()]

df['tx_fee_shift'] = df['tx_fee'].shift(1)

df['tx_fee_rate'] = ((df['tx_fee'] / df['tx_fee_shift']) * 100)

df['tx_fee_rategmean'] = (df['tx_fee_rate']).rolling(window=days, min_periods=3).apply(stats.gmean, raw=True) - 100

trace1 = go.Scatter(x=df['day'], y=df['tx_fee_rategmean'], name='MPE Rate')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='TFE Rate',
    yaxis=dict(
        title='TFE'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 3.3. FDI - Fee Distortion Index (Longo Prazo)

$$FDI = \frac{Taxa de Transacao} {Total de Transacoes}$$

- Valores altos sinalizam distorcoes nas taxas de transacao, o que indica fragilidade da rede

*Data Source:* https://bitcoinvisuals.com/

In [8]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

days = 5

s = requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df = df[df['price_btc'].notnull()]

df['tx_fee'] = df['tx_fee_mean_median'] * df['price_btc']

df['fdi'] =  (df['tx_fee'] / df['tx_count_total_median'])

trace1 = go.Scatter(x=df['day'], y=df['fdi'].rolling(days).mean(), name='FDI')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='FDI',
    yaxis=dict(
        title='FDI',
        type='log'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

In [9]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

days = 5

s = requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df = df[df['price_btc'].notnull()]

df['tx_fee'] = df['tx_fee_mean_median'] * df['price_btc']

df['fdi^-1'] = df['tx_count_total_median'] / df['tx_fee']

trace1 = go.Scatter(x=df['day'], y=df['fdi^-1'].rolling(days).mean(), name='FDI^-1')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='FDI^-1',
    yaxis=dict(
        title='FDI^-1',
        type='log'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

### 4. Atributo: Sentimento

- Ciclo de Mercado:
<img width="600" src="./ciclo-mercado.png" alt="Latest Crypto Fear & Greed Index" />

---

- Ciclo de Sentimento:
<img width="500" src="./ciclo-sentimento.png" alt="Latest Crypto Fear & Greed Index" />

##### 4.1. Fear and Greed Index (Curto Prazo)

<img width="300" src="https://alternative.me/crypto/fear-and-greed-index.png" alt="Latest Crypto Fear & Greed Index" />

- Extreme Greed = Vuneravel a quedas
- Extreme Fear = Suscetivel a altas

*Data Source:*
- https://alternative.me/crypto/fear-and-greed-index/
- https://alternative.me/crypto/fear-and-greed-index/#fng-history

##### 4.2 Shorts Level BTC Bitfinex (Curto Prazo)

- Muito Alto: Bear Trap - Panico - Short Squeeze
- Muito Baixo: Bull Trap - Euforia

*Data Source:* https://www.tradingview.com/

In [10]:
%%html
<!-- TradingView Widget BEGIN -->
<div id="tv-user-info-52ce4"></div>
<script type="text/javascript" src="https://s3.tradingview.com/tv.js"></script>
<script type="text/javascript">
new TradingView.chart({
    "container_id": "tv-user-info-52ce4",
    "chart": "ci6MtCBL",
    "width": "100%"
});
</script>
<!-- TradingView Widget END -->

### 5. Atributo: Acao dos Precos/Grau de Conviccao dos Players

##### 5.1 Bid/Ask Sum 10% Range - Paredao de Compra/Venda (Curto/Medio Prazo)

- Analisar extremos e grandes distorcoes
- Paredao de compra/venda

*Data Source:* https://data.bitcoinity.org/markets/bidask_sum/all/USD/coinbase?bp=10&bu=b&r=day&t=m

In [11]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://data.bitcoinity.org/export_data.csv?bp=10&bu=b&currency=USD&data_type=bidask_sum&exchange=coinbase&r=day&t=m&timespan=all"

s = requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

days = 1

trace1 = go.Scatter(x=df['Time'], y=df['asks'].rolling(days).mean(), name='Ask', marker=dict(color='rgb(214, 39, 40)'))

trace2 = go.Scatter(x=df['Time'], y=df['bids'].rolling(days).mean(), name='Bid', marker=dict(color='rgb(44, 160, 44)'))

trace3 = go.Scatter(x=df['Time'], y=df['price'], name='Price', yaxis='y2', marker=dict(color='#ff7600'))

data = [trace1, trace2, trace3]

layout = go.Layout(
    title='Bid/Ask Sum 10%',
    yaxis=dict(
        title='Bid/Ask Sum [BTC]',
#         type='log'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 5.2 Bitcoin Price Volatility (Curto Prazo)

$$Volatility_i = \frac{Valor de Mercado_i - Valor de Mercado_{i-1}} {Valor de Mercado_{i-1}}$$

- Niveis extremos levam a fim de tendencias de alta ou de baixa
- Pode indicar Panico/Euforia

- [Bitcoin 60 days Price Volatility Chart](http://charts.woobull.com/bitcoin-volatility/)

*Data Source:* https://bitcoinvisuals.com/static/data/data_daily.csv

In [12]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

df = pd.read_csv(io.StringIO(requests.get(url).content.decode('utf-8')), parse_dates=[0])

df = df[df['day'] > '2010-12-01']

df['last_price'] = df['price_btc'].shift(1)

df['volatility'] = ((df['price_btc'] - df['last_price']) / df['last_price']).abs() * 100

trace1 = go.Scatter(x=df['day'], y=df['volatility'], name='Volatility')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='Volatility',
    yaxis=dict(
        title='Volatility (%)',
#         type='log'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

In [13]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from scipy import stats

url = "https://bitcoinvisuals.com/static/data/data_daily.csv"

df = pd.read_csv(io.StringIO(requests.get(url).content.decode('utf-8')), parse_dates=[0])

df = df[df['price_btc'].notnull()]

df['last_price'] = df['price_btc'].shift(1)

df['volatility'] = ((df['price_btc'] - df['last_price']) / df['last_price']).abs() * 100

trace1 = go.Scatter(x=df['day'], y=df['volatility'].rolling(30).mean(), name='30 Days Average Volatility')

trace2 = go.Scatter(x=df['day'], y=df['price_btc'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='30 Days Average Volatility',
    yaxis=dict(
        title='Volatility (%)',
#         type='log'
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 5.3 Volume Ajustado (Curto Prazo)

- Verificar verdadeiros suportes e resistencias
- Final de mercados de baixa apresentam o volume secando
- Volume seca -> baixa convicao -> volume explode na compra -> alta conviccao

*Data Source:* [Coinmetrics](https://coinmetrics.io/charts/#assets=btc_roll=14_left=adjustedTxVolume_zoom=1367107200000,1551830400000)

In [14]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
init_notebook_mode(connected=True)

url = 'https://coinmetrics.io/data/btc.csv'
days = 30

s=requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['adjustedTxVolume(USD)14days'] = df['adjustedTxVolume(USD)'].rolling(window=days).mean()

df = df[df['adjustedTxVolume(USD)14days'].notnull()]

trace1 = go.Scatter(x=df['date'], y=df['adjustedTxVolume(USD)14days'], name='Adj Volume 14 Days Average')

trace2 = go.Scatter(x=df['date'], y=df['price(USD)'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='Adjusted Volume 14 Days Average',
    yaxis=dict(
        title='Volume (USD)',
        type='log',
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 5.4 VIBP - Volume Indexado pelo Preco (Curto/Medio prazo)

$$VIBP = \frac{Volume Ajustado} {Valor de Mercado}$$

- Proxy de final de ciclo
- Mudanca de trend indica final de bull ou bear market

*Datasource:* https://coinmetrics.io/data/btc.csv

In [15]:
import pandas as pd
import io
import requests
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
init_notebook_mode(connected=True)

url = 'https://coinmetrics.io/data/btc.csv'
days = 30

s=requests.get(url).content

df = pd.read_csv(io.StringIO(s.decode('utf-8')), parse_dates=[0])

df['VIBP'] = (df['adjustedTxVolume(USD)'] / df['price(USD)']).rolling(window=days).mean()

df = df[df['VIBP'].notnull()]

trace1 = go.Scatter(x=df['date'], y=df['VIBP'], name='VIBP')

trace2 = go.Scatter(x=df['date'], y=df['price(USD)'], name='Price', yaxis='y2')

data = [trace1, trace2]

layout = go.Layout(
    title='Volume Indexed by Price',
    yaxis=dict(
        title='VIBP',
        type='log',
    ),
    yaxis2=dict(
        title='Price',
        overlaying='y',
        side='right',
        type='log',
        tickangle=50,
        tickvals=[1,10,100,1e3,2e4]
    )
)

fig = go.Figure(data=data, layout=layout)
iplot(fig)

##### 5.5 Seletividade Top Coins (Curto/Curtissimo prazo)

- Todas sobem ou todas descem = Alta conviccao ou vigor na tendencia de alta/baixa
- Poucas sobem ou poucas descem = Baixa conviccao ou esgotamente na tendencia de alta/baixa

*Datasources:* 
- [Barchart](https://www.barchart.com/crypto/performance-leaders?viewName=chart&timeFrame=5d)
- [Coin360](https://coin360.com/)
- [CryptoCompare](https://www.cryptocompare.com/)
- [Coin Market Cap](https://www.coinmarketcap.com/)

##### 5.6 Zonas de Valor

- Grau de Conviccao
- Regra da Minoria
- Elevado Range e Volume
- Alta
    - Formacao de Suporte
- Baixa
    - Formacao de Resistencia